In [ ]:
import random

# The tsdk_namespace provides convenient access to most SDK classes/variables.
from treble_tsdk.tsdk import TSDK, TSDKCredentials
# Here we import the tsdk_namespace as 'treble'.
from treble_tsdk import treble
# The display_data module provides functions that can be used to display many SDK datastructures as trees or tables.
# Here we import the display_data module as 'dd'.
from treble_tsdk import display_data as dd

# at this step, you will need your credentials
tsdk = TSDK(TSDKCredentials.from_file('path/to/credentials'))
# if you have configured the path to your credentials automatically, you may simply call
#tsdk = TSDK()

# check for updates
import treble_tsdk
print(f'Current version: {treble_tsdk.__version__}')

In [ ]:
# Check what projects were created by your credentials
projects = tsdk.list_my_projects()
# If this is your first time running the notebook, this table will be empty. 
dd.as_table(projects)

# create a project with a given name, and check that it has been added to your list of projects
tsdk.create_project("My Unique Project Name")
projects = tsdk.list_my_projects()
# now that you have created a project, this table will show the My Unique Project Name project
dd.as_table(projects)

# retrieve the project by name
project = tsdk.get_by_name("My Unique Project Name")

In [ ]:
# Create a shoebox room
room = treble.GeometryDefinitionGenerator.create_shoebox_room(
    width_x=3,
    depth_y=6,
    height_z=2,
    join_wall_layers=True,
)

# get furniture components
sofa = tsdk.geometry_component_library.query(group="sofa")[1]
chair = tsdk.geometry_component_library.query(group="chair")[1]
table = tsdk.geometry_component_library.query(group="table")[0]

# define positions for the furniture and add the objects to the room
sofa_pos = treble.Vector3d(1.5, 5.5, 0)
room.add_geometry_component("my_comfy_sofa", sofa, treble.Transform3d(sofa_pos, treble.Rotation(0, 0, 0)))

chair1_pos = sofa_pos + treble.Vector3d(-1, -3.2, 0)
chair2_pos = sofa_pos + treble.Vector3d(0, -3.5, 0)
chair3_pos = sofa_pos + treble.Vector3d(0, -2.7, 0)

room.add_geometry_component("my_chair1", chair, treble.Transform3d(chair1_pos, treble.Rotation(-135, 0, 0)))
room.add_geometry_component("my_chair2", chair, treble.Transform3d(chair2_pos, treble.Rotation(-90, 0, 0)))
room.add_geometry_component("my_chair3", chair, treble.Transform3d(chair3_pos, treble.Rotation(60, 0, 0)))

table_pos = treble.Vector3d(1, 4, 0)
room.add_geometry_component("my_table", table, treble.Transform3d(table_pos, treble.Rotation(0, 0, 0)))

# plot the room
room.plot()

# add the room to the project
model = project.add_model("example room", room)

#check that the model has been added to the project
dd.display(project.get_models())

In [ ]:
# Get a list with all materials associated with the organization
all_materials = tsdk.material_library.get()

# Remove materials that are user-generated
database_materials = [material for material in all_materials if material["organizationId"] == None]

# Grab a random material for every layer
material_assignment = [treble.MaterialAssignment(layer, random.choice(database_materials)) for layer in model.layer_names]

# print the random assignment
for l in material_assignment:
    print(l.material_name)

In [ ]:
# first check what the layer names are
for layer in model.layer_names:
    print(layer)

# Create a dictionary associating layer names with acceptable material names
layer_to_search = {
    "shoebox_walls": "gypsum", #any gypsum material is acceptable
    "shoebox_floor": "carpet", #any carpeting is acceptable
    "shoebox_ceiling": "gypsum",
    "Furniture/Couch C": "85", #grab a flat 85% absorption for the couch
    "Furniture/Dining table": "wood", # any wood or wooden furnitures is acceptable
    "Furniture/Chair A": "wood",
}

# create an empty material assignment before the loop
material_assignment = []

# grab a random material from the default materials that comes closer to a realistic assignment
for layer in model.layer_names:
    if layer in layer_to_search:
        search_string = layer_to_search[layer]
        matches = [
            m for m in database_materials
            if search_string.lower() in m.name.lower()
        ]
        if matches:
            material_assignment.append(
                treble.MaterialAssignment(layer, random.choice(matches))
            )

# show the material assignment
dd.display(material_assignment)

In [71]:
# create a list of receivers and sources
receivers = [treble.Receiver(1,1,1.2,treble.ReceiverType.mono,"receiver_1"), treble.Receiver(1,5,1.2,treble.ReceiverType.mono,"receiver_2")]
source = [treble.Source(0.25,0.5,1.5,treble.SourceType.omni,"source_1"), treble.Source(2.25,2,1.3,treble.SourceType.omni,"source_2")]

In [ ]:
sim_def = treble.SimulationDefinition(
        name="Simulation_1", # unique name of the simulation
        simulation_type=treble.SimulationType.ga, # the type of simulation 
        model=model, # the model we created in an earlier step
        energy_decay_threshold=40, # simulation termination criteria - the simulation stops running after -40 dB of energy decay
        receiver_list=receivers, 
        source_list=source,
        material_assignment=material_assignment 
)

# double check that all the receivers and sources fall within the room
sim_def.remove_invalid_receivers()
sim_def.remove_invalid_sources()

# plot the simulation before adding it to the project
sim_def.plot()

# create a simulation from the definition
simulation = project.add_simulation(sim_def)

In [ ]:
simulation.start()
simulation.as_live_progress()

In [ ]:
# download the results
results_object = simulation.download_results(f'results/{simulation.name}')

# begin to explore the results
results_object.plot()

# isolate the data from a single impulse response
this_result = results_object.get_mono_ir(source=simulation.sources[0],receiver=simulation.receivers[1])
this_ir = this_result.data
this_tvec = this_result.time

this_result.plot()